In [1]:
import pandas as pd
import datetime
import numpy as np
import random
from signals import * #потом удалить

In [2]:
class trandeVoter():

    def __init__(self,name):
       
        self.name = name # просто имя
        self.trandeValuesList = ['up','none','down'] #словарь трегдов
        self.matrixAmounts = None # матрица сумм
        self.keysMatrixAmounts = None #ключи матрицы сумм, техническое поле
        self.matrixProbability = None # матрица вероятностей
        
    
    #функция которая создает df с заданным набором колонок и индексов. индексы - уникальные соотношения 
    def createDFbyNames(self, namesIndex, namesColoms,defaultValue=0.0):
        df = pd.DataFrame(dict.fromkeys(namesColoms, [defaultValue]*pow(3,len(namesIndex))),
                          index=pd.MultiIndex.from_product([self.trandeValuesList]*len(namesIndex), names=namesIndex)
                            #,columns=namesColoms
                        )
        return(df)
    
    #создание матрицы сумм с дефолтным значением
    def createMatrixAmounts(self,namesIndex: list) -> pd.DataFrame():
        self.matrixAmounts = self.createDFbyNames(namesIndex,self.trandeValuesList,0)
        self.keysMatrixAmounts = self.matrixAmounts.to_dict('tight')['index_names']
        self.createMatrixProbability(namesIndex)
        return(self.matrixAmounts)
    
    #создание матрицы вероятностей с дефолтным значением
    def createMatrixProbability(self,namesIndex: list) -> pd.DataFrame():
        self.matrixProbability = self.createDFbyNames(namesIndex,self.trandeValuesList)
        return(self.matrixProbability)
    
    #установка значений в матрицы сумм. signalDecisions - значения индикаторов key:value; trande - реальное значение
    def setDecisionBySignals(self,signalDecisions: dict,trande: str) -> None:
        buff=[]
        for i in self.keysMatrixAmounts:
            buff.append(signalDecisions[i])
        self.matrixAmounts.loc[tuple(buff),trande] += 1
        
    #заполнение матрицы вероятностей вычисляемыми значениями из матрицы сумм
    def generateMatrixProbability(self) -> None:
        for i in range(self.matrixAmounts.shape[0]):
            rowSum=sum(self.matrixAmounts.iloc[i])
            self.matrixProbability.iloc[i]['up'] = (self.matrixAmounts.iloc[i]['up'] / rowSum)
            self.matrixProbability.iloc[i]['none'] = self.matrixAmounts.iloc[i]['none'] / rowSum
            self.matrixProbability.iloc[i]['down'] = self.matrixAmounts.iloc[i]['down'] / rowSum

    #получение рещения из матрицы вероятностей по заданным значениям сигналов
    def getDecisionBySignals(self,signalDecisions: dict) -> dict:
        ans = {}
        spliceSearch =self.matrixProbability.xs(tuple(signalDecisions.values()),
                                                       level=list(signalDecisions.keys())
                                                      ) 
        ans['probability'] = spliceSearch.to_dict('records')[0]
        ans['trande'] = spliceSearch.iloc[0].idxmax()
        return ans
    
    #получение матриц вероятностей и суммы в видей словарей
    def getMatrixDict(self) -> dict:
        ans={}
        ans['amounts'] = self.matrixAmounts.to_dict('tight')
        ans['probability'] = self.matrixProbability.to_dict('tight')
        return ans
    
    #установка матриц вероятностей и суммы в видей словарей
    def setMatrixDict(self,matrixDict: dict) -> dict:
        if matrixDict['amounts'] != None:
            self.matrixAmounts = pd.DataFrame.from_dict(y['amounts'], orient='tight')
        if matrixDict['probability'] != None:
            self.matrixProbability = pd.DataFrame.from_dict(y['probability'], orient='tight') 

In [3]:
reqSig={
    'BB1':{
        'className':signal_BB,
        'indParams':{'MeanType':'SMA','window':15,'valueType':'close','kDev':2.5},
        'signalParams':{'source':'close','target':'close'},
        'batchSize':15
    },
    'BB2':{
        'className':signal_BB,
        'indParams':{'MeanType':'SMA','window':15,'valueType':'close','kDev':2.5},
        'signalParams':{'source':'close','target':'close'},
        'batchSize':20
    }
}



In [4]:
reqDS={'BB1':'up','BB2':'none'}

In [7]:
reqCreate=list(reqSig.keys())
reqCreate

['BB1', 'BB2']

In [8]:
t=trandeVoter('piu')
o=t.createMatrixAmounts(['BB1', 'BB2'])
o

up  none  down
BB1  BB2                 
up   up     0     0     0
     none   0     0     0
     down   0     0     0
none up     0     0     0
     none   0     0     0
     down   0     0     0
down up     0     0     0
     none   0     0     0
     down   0     0     0

In [9]:
for i in range(100000):
    t.setDecisionBySignals({'BB1':random.choice(['up','down','none']),
                            'BB2':random.choice(['up','down','none'])},
                           random.choice(['up','down','none']))
    

In [10]:
t.matrixAmounts

up  none  down
BB1  BB2                   
up   up    3673  3602  3728
     none  3712  3700  3715
     down  3682  3621  3766
none up    3600  3657  3711
     none  3636  3720  3719
     down  3606  3700  3785
down up    3745  3743  3774
     none  3606  3810  3688
     down  3782  3801  3718

In [11]:
t.generateMatrixProbability()

In [577]:
t.matrixProbability


up      none      down
BB1  BB2                               
up   up    0.337273  0.334050  0.328678
     none  0.322725  0.336534  0.340741
     down  0.336122  0.334952  0.328926
none up    0.334929  0.325808  0.339263
     none  0.327491  0.341055  0.331454
     down  0.330258  0.342108  0.327635
down up    0.336870  0.334784  0.328346
     none  0.328860  0.334675  0.336464
     down  0.326240  0.338233  0.335528

In [14]:
t.setMatrixDict(y)

In [15]:
t.getDecisionBySignals(reqDS)

{'probability': {'up': 0.3336029477846679,
  'none': 0.33252448997932954,
  'down': 0.33387256223600253},
 'trande': 'down'}

In [13]:
y = t.getMatrixDict()
y

{'amounts': {'index': [('up', 'up'),
   ('up', 'none'),
   ('up', 'down'),
   ('none', 'up'),
   ('none', 'none'),
   ('none', 'down'),
   ('down', 'up'),
   ('down', 'none'),
   ('down', 'down')],
  'columns': ['up', 'none', 'down'],
  'data': [[3673, 3602, 3728],
   [3712, 3700, 3715],
   [3682, 3621, 3766],
   [3600, 3657, 3711],
   [3636, 3720, 3719],
   [3606, 3700, 3785],
   [3745, 3743, 3774],
   [3606, 3810, 3688],
   [3782, 3801, 3718]],
  'index_names': ['BB1', 'BB2'],
  'column_names': [None]},
 'probability': {'index': [('up', 'up'),
   ('up', 'none'),
   ('up', 'down'),
   ('none', 'up'),
   ('none', 'none'),
   ('none', 'down'),
   ('down', 'up'),
   ('down', 'none'),
   ('down', 'down')],
  'columns': ['up', 'none', 'down'],
  'data': [[0.3338180496228301, 0.3273652640189039, 0.33881668635826595],
   [0.3336029477846679, 0.33252448997932954, 0.33387256223600253],
   [0.33264070828439785, 0.3271298220254766, 0.3402294696901256],
   [0.3282275711159737, 0.33342450765864334

In [16]:
ddf = pd.DataFrame.from_dict(y['amounts'], orient='tight')
ddf

up  none  down
BB1  BB2                   
up   up    3673  3602  3728
     none  3712  3700  3715
     down  3682  3621  3766
none up    3600  3657  3711
     none  3636  3720  3719
     down  3606  3700  3785
down up    3745  3743  3774
     none  3606  3810  3688
     down  3782  3801  3718

In [17]:
t.matrixProbability.iloc[0]['up'] = (t.matrixProbability.iloc[0]['up'] / (sum(t.matrixProbability.iloc[0])))
t.matrixProbability

up      none      down
BB1  BB2                               
up   up    0.333818  0.327365  0.338817
     none  0.333603  0.332524  0.333873
     down  0.332641  0.327130  0.340229
none up    0.328228  0.333425  0.338348
     none  0.328307  0.335892  0.335801
     down  0.325128  0.333604  0.341268
down up    0.332534  0.332357  0.335109
     none  0.324748  0.343120  0.332133
     down  0.334661  0.336342  0.328997

In [18]:
t.matrixProbability['trandе']

KeyError: 'trandе'

In [19]:
random.choice(['up','down','none'])

'up'

In [20]:
t.setDecisionBySignals(reqDS,'up')

In [21]:
#t.matrixAmounts.at(bbb,'up')
    
t.matrixAmounts.iloc[0]

up      3673
none    3602
down    3728
Name: (up, up), dtype: int64

In [22]:
for i in t.matrixAmounts.iloc[0]:
    print (i)

3673
3602
3728


In [23]:
(t.matrixAmounts.iloc[0]).idxmax()

'down'

In [24]:
t.matrixAmounts

up  none  down
BB1  BB2                   
up   up    3673  3602  3728
     none  3713  3700  3715
     down  3682  3621  3766
none up    3600  3657  3711
     none  3636  3720  3719
     down  3606  3700  3785
down up    3745  3743  3774
     none  3606  3810  3688
     down  3782  3801  3718

In [25]:
o.xs(('up','down'), level=['BB1','BB2'])['up'].iloc[0]

#oldValue = o.xs(('up','down'), level=['BB1','BB2'])['up']

#o=o.replace(oldValue,oldValue.iloc[0]+1) 
#o.xs(('up','down'), level=['BB1','BB2'])

3682

In [26]:
o.xs(('up','down'), level=['BB1','BB2'], drop_level=False)#.iloc[0].loc['up']=2#.at['up']=4

up  none  down
BB1 BB2                   
up  down  3682  3621  3766

In [27]:
o.xs(('up','down'), level=['BB1','BB2']).iloc[0].at['up']

3682

In [28]:
o.loc['up'].loc['down']

up      3682
none    3621
down    3766
Name: down, dtype: int64

In [29]:
bbb=tuple(['up','down'])
bbb

('up', 'down')

In [30]:
o.loc[bbb,]

up      3682
none    3621
down    3766
Name: (up, down), dtype: int64

In [31]:
o.at[bbb, 'up']+=1
o

up  none  down
BB1  BB2                   
up   up    3673  3602  3728
     none  3712  3700  3715
     down  3683  3621  3766
none up    3600  3657  3711
     none  3636  3720  3719
     down  3606  3700  3785
down up    3745  3743  3774
     none  3606  3810  3688
     down  3782  3801  3718

In [32]:
o.loc[bbb]

up      3683
none    3621
down    3766
Name: (up, down), dtype: int64

In [33]:
dict(zip(['a','b','c'], [1,2,3]))

{'a': 1, 'b': 2, 'c': 3}